In [ ]:
%%capture
!pip install datasets
!pip install --upgrade transformers
!pip install torchaudio
!pip install huggingface_hub
!pip install jiwer evaluate wandb
!pip install librosa
!pip install accelerate -U

In [ ]:
!pip install transformers[torch]
!pip install accelerate==0.26.0

In [1]:
import os
import re
import unicodedata
import json
import numpy as np
import pandas as pd
import wandb
import librosa

from datasets import load_dataset, DatasetDict, Audio
from transformers import (
    Wav2Vec2CTCTokenizer,
    Wav2Vec2FeatureExtractor,
    Wav2Vec2Processor,
    Wav2Vec2ForCTC,
    TrainingArguments,
    Trainer,
    EarlyStoppingCallback,
)
import evaluate
import torch
from dataclasses import dataclass
from typing import Dict, List, Union


In [2]:
num_proc = os.cpu_count()//2
num_dataloaders = os.cpu_count()//2

print(f"Cpu count: {os.cpu_count()}\nNum proc: {num_proc}\nNum dataloaders: {num_dataloaders}")

Cpu count: 96
Num proc: 48
Num dataloaders: 48


In [ ]:
from huggingface_hub import notebook_login

notebook_login()

In [3]:
from datasets import load_dataset, Audio

data_files = {
    'train': 'train_data.csv',
    'validation': 'validation_data.csv',
    'test': 'test_data.csv'
}

dataset = load_dataset('csv', data_files=data_files)


In [4]:
columns_to_keep = ['audio_path', 'sentence', 'audio_len', 'transcript_len']
dataset = dataset.map(lambda batch: {k: batch[k] for k in columns_to_keep}, remove_columns=dataset['train'].column_names)


In [5]:
dataset = dataset.rename_column('audio_path', 'audio')
dataset = dataset.cast_column('audio', Audio(sampling_rate=16_000))

In [6]:
train_dataset = dataset['train']
eval_dataset = dataset['validation']
test_dataset = dataset['test']


In [7]:
def preprocess_text(batch):
    # Convert to lowercase
    batch['sentence'] = batch['sentence'].lower()
    
    # Normalize text
    batch['sentence'] = unicodedata.normalize('NFKC', batch['sentence'])
    batch['sentence'] = re.sub(r"[\’\ʻ\ʼ\ʽ\‘]", "'", batch['sentence'])
    
    # Remove punctuation and special characters (except apostrophes)
    batch['sentence'] = re.sub(r"[^\w\s']", '', batch['sentence'])
    batch['sentence'] = re.sub(r'_', ' ', batch['sentence'])
    
    # Remove excessive whitespace
    batch['sentence'] = ' '.join(batch['sentence'].split())
    
    return batch


train_dataset = train_dataset.map(preprocess_text)
eval_dataset = eval_dataset.map(preprocess_text)
test_dataset = test_dataset.map(preprocess_text)

In [8]:
def get_len(batch):
    # Compute audio length if not already computed
    if batch.get('audio_len') is None or batch['audio_len'] == 0.0:
        audio = batch['audio']
        audio_len = librosa.get_duration(y=audio['array'], sr=audio['sampling_rate'])
        batch['audio_len'] = audio_len
    
    # Compute transcript length if not already computed
    if batch.get('transcript_len') is None or batch['transcript_len'] == 0:
        batch['transcript_len'] = len(batch['sentence'])
    
    # Compute length ratio
    batch['len_ratio'] = float(batch['audio_len']) / float(batch['transcript_len']) if batch['transcript_len'] > 0 else 0.0
    
    # Number of feature vectors (assuming 20ms frame shift)
    batch['num_feature_vecs'] = int(np.round(batch['audio_len'] * 1000 / 20))
    
    return batch


train_dataset = train_dataset.map(get_len)
eval_dataset = eval_dataset.map(get_len)
test_dataset = test_dataset.map(get_len)


In [9]:
print(f"Train dataset size: {len(train_dataset)} samples")
print(f"Validation dataset size: {len(eval_dataset)} samples")
print(f"Test dataset size: {len(test_dataset)} samples")

print(f"Total training audio duration: {sum(train_dataset['audio_len']) / 3600:.2f} hours")
print(f"Total validation audio duration: {sum(eval_dataset['audio_len']) / 3600:.2f} hours")
print(f"Total test audio duration: {sum(test_dataset['audio_len']) / 3600:.2f} hours")


Train dataset size: 3151 samples
Validation dataset size: 647 samples
Test dataset size: 648 samples
Total training audio duration: 20.00 hours
Total validation audio duration: 4.10 hours
Total test audio duration: 4.06 hours


In [10]:
def extract_all_chars(batch):
    all_text = ' '.join(batch['sentence'])
    vocab = list(set(all_text))
    return {'vocab': [vocab]}

vocab_list = train_dataset.map(
    extract_all_chars,
    batched=True,
    batch_size=-1,
    remove_columns=train_dataset.column_names
)

vocab_set = set()
for vocab in vocab_list['vocab']:
    vocab_set.update(vocab)

# Ensure space character is included
if ' ' not in vocab_set:
    vocab_set.add(' ')

alphabet = ''.join(sorted(vocab_set))
print(f"Alphabet: {alphabet}")


Alphabet:  '169abcdefghijklmnopqrstuvwyzàŋ


In [11]:
vocab_dict = {char: idx for idx, char in enumerate(sorted(vocab_set))}

# Replace space with word delimiter token '|'
vocab_dict['|'] = vocab_dict[' ']
del vocab_dict[' ']

# Add special tokens
vocab_dict['[UNK]'] = len(vocab_dict)
vocab_dict['[PAD]'] = len(vocab_dict)

# Save the vocabulary dictionary to a JSON file
with open('vocab.json', 'w') as vocab_file:
    json.dump(vocab_dict, vocab_file)


In [12]:
tokenizer = Wav2Vec2CTCTokenizer(
    'vocab.json',
    unk_token='[UNK]',
    pad_token='[PAD]',
    word_delimiter_token='|'
)

feature_extractor = Wav2Vec2FeatureExtractor(
    feature_size=1,
    sampling_rate=16_000,
    padding_value=0.0,
    do_normalize=True,
    return_attention_mask=True
)

processor = Wav2Vec2Processor(
    feature_extractor=feature_extractor,
    tokenizer=tokenizer
)


/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1617: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be deprecated in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


In [13]:
def prepare_dataset(batch):
    # Process audio
    audio = batch['audio']
    batch['input_values'] = processor(
        audio['array'],
        sampling_rate=audio['sampling_rate']
    ).input_values[0]
    
    # Process transcript
    batch['labels'] = processor(
        text=batch['sentence']
    ).input_ids
    return batch


In [14]:
train_dataset = train_dataset.map(prepare_dataset, remove_columns=['audio', 'sentence'])
eval_dataset = eval_dataset.map(prepare_dataset, remove_columns=['audio', 'sentence'])
test_dataset = test_dataset.map(prepare_dataset, remove_columns=['audio', 'sentence'])


In [15]:
@dataclass
class DataCollatorCTCWithPadding:
    processor: Wav2Vec2Processor
    padding: Union[bool, str] = True

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # Split inputs and labels
        input_features = [{'input_values': feature['input_values']} for feature in features]
        label_features = [{'input_ids': feature['labels']} for feature in features]

        # Pad inputs
        batch = self.processor.pad(
            input_features,
            padding=self.padding,
            return_tensors='pt'
        )

        # Pad labels
        labels_batch = self.processor.pad(
            labels=label_features,
            padding=self.padding,
            return_tensors='pt'
        )

        # Replace padding with -100 to ignore loss calculation for padding
        labels = labels_batch['input_ids'].masked_fill(labels_batch.attention_mask.ne(1), -100)

        batch['labels'] = labels

        return batch

data_collator = DataCollatorCTCWithPadding(processor=processor, padding=True)


In [16]:
wer_metric = evaluate.load('wer')
cer_metric = evaluate.load('cer')


In [17]:
def compute_metrics(pred):
    pred_logits = pred.predictions
    pred_ids = np.argmax(pred_logits, axis=-1)

    # Replace -100 in labels as we can't decode them
    label_ids = pred.label_ids
    label_ids[label_ids == -100] = processor.tokenizer.pad_token_id

    # Decode predictions and references
    pred_str = processor.batch_decode(pred_ids)
    label_str = processor.batch_decode(label_ids, group_tokens=False)

    wer = wer_metric.compute(predictions=pred_str, references=label_str)
    cer = cer_metric.compute(predictions=pred_str, references=label_str)

    return {'wer': wer, 'cer': cer}


In [18]:
model_checkpoint = "facebook/wav2vec2-xls-r-300m"  # You can use a different checkpoint if desired

model = Wav2Vec2ForCTC.from_pretrained(
    model_checkpoint,
    attention_dropout=0.1,
    hidden_dropout=0.1,
    feat_proj_dropout=0.0,
    mask_time_prob=0.05,
    layerdrop=0.1,
    ctc_loss_reduction='mean',
    pad_token_id=processor.tokenizer.pad_token_id,
    vocab_size=len(processor.tokenizer),
)


/usr/local/lib/python3.10/dist-packages/torch/_utils.py:831: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  return self.fget.__get__(instance, owner)()
Some weights of Wav2Vec2ForCTC were not initialized from the model checkpoint at facebook/wav2vec2-xls-r-300m and are newly initialized: ['lm_head.bias', 'lm_head.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [19]:
model.freeze_feature_encoder()


In [20]:
round(sum(train_dataset['audio_len']) / 3600)

20

In [21]:
# Define your dataset and experiment details
dataset = 'yogera'  # Replace with actual dataset name
language = 'lg'  # Replace with the language you are working with
sample_hours = round(sum(train_dataset['audio_len']) / 3600)  # Calculate total training hours
version = 'v1'  # Version of your fine-tuned model
batch_size = 8  # Adjust based on your GPU capacity
grad_acc = 1
eval_batch_size = batch_size // 2
epochs = 100  # Adjust as needed
output_dir = f"{model_checkpoint.split('/')[-1]}-{dataset}-{language}-{sample_hours}hrs-{version}"

# Initialize WandB
wandb.init(
    project="ASR Africa",
    entity="asr-africa-research-team",
    name=output_dir,
)


wandb: Using wandb-core as the SDK backend. Please refer to https://wandb.me/wandb-core for more information.
wandb: Currently logged in as: sulaiman-kagumire (asr-africa-research-team). Use `wandb login --relogin` to force relogin


In [31]:
training_args = TrainingArguments(
  output_dir=output_dir,
  group_by_length=True,
  per_device_train_batch_size=batch_size,
  per_device_eval_batch_size=eval_batch_size,
  gradient_accumulation_steps=grad_acc,
  eval_strategy="epoch",
  logging_strategy="epoch",
  save_strategy="epoch",
  num_train_epochs=epochs,
  gradient_checkpointing=True,
  fp16=True,
  learning_rate=1e-4,
  lr_scheduler_type='linear',
  warmup_ratio=0.1,
  save_total_limit=2,
  load_best_model_at_end=True,
  metric_for_best_model="wer",
  greater_is_better=False,
  optim='adamw_torch',
  push_to_hub=True,
  hub_model_id=f"asr-africa/{output_dir}",
  hub_private_repo=True,
  dataloader_num_workers=num_dataloaders,
)

In [32]:
trainer = Trainer(
    model=model,
    data_collator=data_collator,
    args=training_args,
    compute_metrics=compute_metrics,
    train_dataset=train_dataset,
    eval_dataset=eval_dataset,
    tokenizer=processor.feature_extractor,
    callbacks=[
        EarlyStoppingCallback(
            early_stopping_patience=10,  # Stop if no improvement after 10 evaluation steps
            early_stopping_threshold=1e-3  # Stop if improvement is less than 0.001
        )
    ],
)


Detected kernel version 5.4.0, which is below the recommended minimum of 5.5.0; this can cause the process to hang. It is recommended to upgrade the kernel to the minimum version or higher.


In [33]:
trainer.train()

wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.


KeyboardInterrupt: 

In [ ]:
from huggingface_hub import HfApi, HfFolder

# Your Hugging Face credentials
repo_id = "sulaimank/yog-transcribed"  # Replace with your actual Hugging Face repository
zip_file = "transcribed_wavs.zip"

# Initialize API and upload
api = HfApi()
api.upload_file(
    path_or_fileobj=zip_file,
    path_in_repo=zip_file,  # Path where the file will be stored in the repo
    repo_id=repo_id,
    repo_type="dataset",  # This is a dataset repository
)

print(f"Uploaded {zip_file} to Hugging Face at {repo_id}")
